# Examples of convolutional network

In [1]:
## Imports
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

D:\ProgramData\Anaconda3\lib\site-packages\h5py\__init__.py:34: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


### Model / Classifier

In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)
  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

### Data loading

In [3]:
# def main(unused_argv):
  # Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz


### Estimator creation

In [4]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001E1C258DF60>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


### Logging hook

In [5]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

In [6]:
# import sys
# sys.version
# sys.version_info

### Training model

In [7]:
# Train the model
with  tf.device("/gpu:0"):
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Saving checkpoints for 20001 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:probabilities = [[0.00000001 0.00000146 0.00112996 0.99885833 0.         0.00000227
  0.         0.00000089 0.00000709 0.00000002]
 [0.00000545 0.00016345 0.0004364  0.9890443  0.00000056 0.0022791
  0.00000025 0.00005459 0.00661967 0.0013962 ]
 [0.00000385 0.00001875 0.98217154 0.00055885 0.00000623 0.00004162
  0.00000618 0.0000048  0.01715473 0.00003358]
 [0.999076   0.00000007 0.00019368 0.00000091 0.00000005 0.00043131
  0.00005717 0.00000046 0.00023675 0.00000359]
 [0.00000441 0.9975044  0.00009085 0.00043553 0.00014069 0.00002381
  0.00000558 0.00050569 0.00049538 0.00079362]
 [0.00321509 0.00022416 0.06286046 0.18110693 0.00512874 0.01614578
  0.00149062 0.00042675 0.5804033  0.14899813]
 [0.9977781  0.00000001 0.00000075 0.00000143 0.00000001 0.00000

INFO:tensorflow:loss = 0.05404055, step = 20001
INFO:tensorflow:probabilities = [[0.00234    0.00034794 0.00008142 0.01439372 0.00051463 0.9785903
  0.00196492 0.00000942 0.00119749 0.00056012]
 [0.00001312 0.00017667 0.00050723 0.04334937 0.00000066 0.00111754
  0.00000104 0.00000293 0.95478505 0.00004637]
 [0.99919146 0.         0.00002196 0.00000005 0.         0.00076976
  0.00000155 0.00000007 0.00000978 0.00000553]
 [0.00003444 0.00111407 0.00321833 0.00297025 0.21937269 0.02560471
  0.00179707 0.00030623 0.7020907  0.04349153]
 [0.00003992 0.00004865 0.00046409 0.00007996 0.00007924 0.00001934
  0.00012694 0.00000037 0.9991204  0.00002107]
 [0.00000153 0.00000039 0.00033742 0.00000011 0.992243   0.00001435
  0.00668506 0.0000268  0.00024534 0.00044591]
 [0.00000004 0.99981195 0.00000567 0.00001848 0.00003512 0.00000113
  0.00000758 0.00000076 0.0001086  0.00001068]
 [0.00001468 0.00862278 0.01070076 0.0452397  0.82159096 0.00533284
  0.00269453 0.07277475 0.02536862 0.00766031]
 

INFO:tensorflow:global_step/sec: 106.202
INFO:tensorflow:probabilities = [[0.00000921 0.00000188 0.0027035  0.00075006 0.00000185 0.00000075
  0.         0.9962424  0.00000612 0.00028421]
 [0.0047001  0.00820152 0.00165421 0.46595508 0.0001862  0.49827665
  0.00079669 0.00022768 0.01095053 0.00905126]
 [0.00004969 0.00000001 0.00000278 0.00000005 0.00000356 0.00001889
  0.99992466 0.         0.00000039 0.00000001]
 [0.00000375 0.00032661 0.993101   0.0054788  0.00004395 0.00034679
  0.00000635 0.00000652 0.00032258 0.00036356]
 [0.00002685 0.00000006 0.00000539 0.00119535 0.00000154 0.00012444
  0.00000039 0.00000002 0.99863416 0.00001178]
 [0.00012576 0.00001511 0.10772908 0.00009075 0.7599819  0.00041593
  0.12624626 0.00090746 0.00139215 0.0030957 ]
 [0.00004847 0.00000091 0.00000769 0.00001642 0.00004077 0.0000839
  0.00000007 0.99823207 0.00000772 0.00156203]
 [0.00792415 0.00062692 0.02681786 0.00174585 0.78719926 0.0027491
  0.01228306 0.00583593 0.01409539 0.14072248]
 [0.00016

INFO:tensorflow:loss = 0.118250266, step = 20101 (0.943 sec)
INFO:tensorflow:probabilities = [[0.00000027 0.00033266 0.9990439  0.0005874  0.00000018 0.00000082
  0.00001405 0.00000017 0.00002061 0.00000002]
 [0.00022058 0.00001874 0.00001608 0.00132947 0.0000533  0.9973574
  0.00010681 0.00006758 0.00063126 0.00019889]
 [0.00003203 0.00000249 0.00593739 0.00000111 0.99038714 0.00004816
  0.00345433 0.00006811 0.00005638 0.00001281]
 [0.00014257 0.00017806 0.0239734  0.00004013 0.09083488 0.00005569
  0.8830548  0.00048023 0.00116169 0.00007861]
 [0.00001257 0.986832   0.00088841 0.00138323 0.00008179 0.00005809
  0.0003006  0.00010972 0.01030137 0.00003225]
 [0.9982116  0.00000083 0.00014255 0.00007713 0.00000001 0.00153192
  0.00000712 0.0000165  0.00000777 0.00000456]
 [0.00002112 0.99620134 0.00018168 0.00004644 0.00006081 0.00000578
  0.00001242 0.00180783 0.00163567 0.00002687]
 [0.0010872  0.00004402 0.00107737 0.2890692  0.0000069  0.65178174
  0.0000186  0.00147575 0.03568428 

INFO:tensorflow:global_step/sec: 114.226
INFO:tensorflow:probabilities = [[0.00001403 0.9986003  0.00012365 0.00009515 0.00002057 0.00003634
  0.00008198 0.00007812 0.00094027 0.00000949]
 [0.99996483 0.         0.00001409 0.00000011 0.00000001 0.00000143
  0.00000011 0.00000022 0.00000675 0.00001235]
 [0.00001543 0.00001845 0.00085126 0.00927339 0.00002705 0.00145302
  0.00004864 0.00003052 0.9879645  0.00031775]
 [0.00011907 0.00011615 0.00018232 0.00848139 0.00007053 0.00132714
  0.00000577 0.00006401 0.968071   0.02156257]
 [0.00007262 0.0000021  0.99620736 0.00091531 0.00007508 0.0000293
  0.00000565 0.00000803 0.00226867 0.00041585]
 [0.99220383 0.00000014 0.00265427 0.00006501 0.00000001 0.00485646
  0.000001   0.00000057 0.000025   0.00019379]
 [0.00022575 0.9588116  0.00111091 0.00006656 0.00023338 0.00028864
  0.02212548 0.00011827 0.01695193 0.00006757]
 [0.00003353 0.00005015 0.00275285 0.9897479  0.00000014 0.00390575
  0.00000163 0.00000046 0.00334245 0.00016517]
 [0.0000

...

INFO:tensorflow:global_step/sec: 99.0598
INFO:tensorflow:probabilities = [[0.9997377  0.00000005 0.0000615  0.00000008 0.00000025 0.00000155
  0.0001932  0.00000014 0.00000548 0.00000008]
 [0.00000773 0.00004763 0.99344504 0.00029452 0.00000753 0.00001872
  0.00000254 0.00012587 0.0060286  0.00002185]
 [0.00000003 0.9999254  0.00000523 0.00000085 0.00000557 0.00000005
  0.00000165 0.00004358 0.00000945 0.00000828]
 [0.00005036 0.01150994 0.00003575 0.87741786 0.00013247 0.00021342
  0.00000022 0.06694678 0.00012291 0.04357031]
 [0.00000003 0.00000002 0.00000095 0.0000003  0.99872273 0.00000335
  0.00000105 0.00002687 0.00001933 0.00122529]
 [0.00000074 0.00001596 0.00021021 0.00091966 0.00002444 0.00015532
  0.0000354  0.00000269 0.9984635  0.00017217]
 [0.00000003 0.         0.00000134 0.00000051 0.         0.
  0.         0.9999852  0.00000004 0.00001288]
 [0.00006625 0.00000969 0.00504974 0.01650878 0.00000463 0.00189906
  0.00009491 0.00011148 0.969192   0.00706341]
 [0.         0.

INFO:tensorflow:loss = 0.031836793, step = 39801 (1.012 sec)
INFO:tensorflow:probabilities = [[0.00000455 0.0001944  0.000085   0.9979824  0.         0.00173157
  0.         0.00000011 0.00000067 0.00000117]
 [0.99975437 0.00000001 0.00003825 0.00000003 0.         0.00017833
  0.00000595 0.00000005 0.00000029 0.00002293]
 [0.9842717  0.00008784 0.00198932 0.00032476 0.00007135 0.00112774
  0.00749099 0.00013208 0.00419352 0.00031074]
 [0.99999547 0.         0.00000049 0.00000001 0.         0.00000017
  0.00000002 0.00000119 0.         0.0000027 ]
 [0.00173773 0.00116342 0.00335327 0.00119249 0.00125674 0.9320361
  0.0212077  0.0012888  0.03665536 0.00010837]
 [0.99984753 0.         0.00000097 0.         0.00000001 0.00000092
  0.00000001 0.00001081 0.00000002 0.00013966]
 [0.0051654  0.8739987  0.00009971 0.00005435 0.05601622 0.00008855
  0.00122236 0.01544869 0.03999846 0.00790751]
 [0.         0.00000003 0.9999994  0.00000028 0.00000004 0.
  0.00000001 0.         0.00000031 0.      

INFO:tensorflow:global_step/sec: 98.196
INFO:tensorflow:probabilities = [[0.         0.         0.0000001  0.99999285 0.         0.00000582
  0.         0.         0.00000008 0.00000109]
 [0.00003378 0.00000026 0.00000016 0.00000012 0.00051494 0.00001795
  0.99941385 0.00000127 0.00001149 0.00000619]
 [0.00000118 0.00000047 0.0001509  0.00004638 0.00000015 0.00000197
  0.00000008 0.00000038 0.9997962  0.00000225]
 [0.00000061 0.9999424  0.00000029 0.00000043 0.00002362 0.00000053
  0.00000099 0.00001809 0.00000774 0.00000534]
 [0.0000003  0.00000007 0.00000042 0.00000154 0.00151862 0.0000001
  0.         0.00085507 0.00000079 0.997623  ]
 [0.00000592 0.0200716  0.0000208  0.00524918 0.02158835 0.00093856
  0.00000455 0.00137802 0.00420609 0.94653696]
 [0.00000056 0.         0.00000813 0.00009405 0.00000008 0.00000361
  0.         0.00000001 0.99986064 0.00003284]
 [0.         0.00000065 0.99999404 0.00000116 0.         0.
  0.         0.         0.00000415 0.        ]
 [0.00004866 0.00

INFO:tensorflow:loss = 0.043383155, step = 39901 (1.015 sec)
INFO:tensorflow:probabilities = [[0.00076963 0.00000338 0.00010636 0.00000302 0.00001061 0.00040568
  0.9982327  0.00000004 0.00046596 0.00000257]
 [0.00000003 0.00000089 0.99962115 0.0003484  0.00000004 0.00000001
  0.         0.00002462 0.00000441 0.00000037]
 [0.         0.         0.00000128 0.00004361 0.00007237 0.00000844
  0.         0.00096211 0.00001292 0.9988992 ]
 [0.00001062 0.00000532 0.00004924 0.00003333 0.99222773 0.00020879
  0.00000536 0.00070843 0.0000107  0.0067406 ]
 [0.9994043  0.         0.00051991 0.         0.00001527 0.00000012
  0.00004112 0.00000175 0.00000178 0.00001571]
 [0.17160791 0.03055974 0.6758936  0.01484785 0.00002156 0.00511121
  0.00032461 0.00042545 0.10112619 0.00008186]
 [0.99765414 0.00000023 0.00126279 0.00000033 0.00058455 0.00000004
  0.00001812 0.00000561 0.0000008  0.00047341]
 [0.00000004 0.00002755 0.99987316 0.00008897 0.0000005  0.00000032
  0.00000034 0.00000001 0.00000904

INFO:tensorflow:Saving checkpoints for 40000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.12000694.


### Evaluating model

In [8]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Starting evaluation at 2018-03-07-09:41:54
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-40000
INFO:tensorflow:Finished evaluation at 2018-03-07-09:41:56
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.98, global_step = 40000, loss = 0.062333174
{'accuracy': 0.98, 'loss': 0.062333174, 'global_step': 40000}
